In [1]:
import numpy as np 
import pandas as pd 
from scipy import stats
import calendar
import matplotlib as plt
import category_encoders as ce
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.model_selection import ShuffleSplit
from sklearn import linear_model
from sklearn.tree import DecisionTreeRegressor
from sklearn.metrics import make_scorer
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction import FeatureHasher
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn import svm

In [2]:
def encode(x): return 1 if x == 'M' else 0

In [3]:
def performance_metric(y_true, y_predict):
    """ Calculates and returns the performance score between 
        true and predicted values based on the metric chosen. """    
    # TODO: Calculate the performance score between 'y_true' and 'y_predict'
    score = r2_score(y_true, y_predict)    
    # Return the score
    return score

In [5]:
tuned_parameters = [{'max_features': ['sqrt', 'log2', None],
                             'max_depth': range(2,1000),
                             }
                            ]
reg = GridSearchCV(DecisionTreeRegressor(), tuned_parameters, cv=5, scoring='neg_mean_squared_error')

In [6]:
def binning(df,colName,labels):
    #Define min and max values:
    #create list by adding min and max to cut_points
    break_points = [df[colName].min()] + [df[colName].describe()[4]] + [df[colName].describe()[5]] + [df[colName].describe()[6]] + [df[colName].max()]

    #labels = ["low","medium","high","very high"]

    #Binning using cut function of pandas
    colBin = pd.cut(df[colName],bins=break_points,labels=labels,include_lowest=True)
    return colBin

In [7]:
df = pd.read_csv('data/train.csv')
labels = ["young","adult","old","elder"]
df['Date']=pd.to_datetime(df['Date'], format='%Y%m', errors='ignore')
#df=df.sort_values('Date')
df['Month'] = df['Date'].dt.month#.apply(lambda x: calendar.month_abbr[x])
df['Gender'] = df.Gender.apply(encode)
df['Age_bin'] = binning(df,"Age",labels)
lb_make = LabelEncoder()
df["Age_code"] = lb_make.fit_transform(df["Age_bin"])
#df['Event_freq']=df.groupby('Event_Code')['Event_Code'].transform('count')
df.head()

UID  Age  Gender       Date Event_Code  Month Age_bin  Age_code
0  Id_e45bbc48   14       0 2012-05-01       8707      5   young         3
1  Id_e45a8472   52       0 2013-05-01       7261      5     old         2
2  Id_e45b20d6   12       0 2012-12-01       1967     12   young         3
3  Id_e45aabad   22       0 2012-11-01       7172     11   young         3
4  Id_e45c5780   73       0 2013-12-01       8100     12   elder         1

In [20]:
#df['Event_Code'].nunique()
mlb = MultiLabelBinarizer()
mlb.fit_transform(df['Event_Code']).shape

(766787, 27)

In [8]:
fh = FeatureHasher(n_features=12, input_type='string')
hashed_features = fh.fit_transform(df['Event_Code'])
hashed_features = hashed_features.toarray()
#pd.concat([df[['Event_Code']], pd.DataFrame(hashed_features)], axis=1).head()
y = pd.DataFrame(hashed_features)

In [9]:
X = df[['Gender','Age_code','Month']].copy()
#y = df[['Event_freq']].copy()

In [31]:
#pat1 = df.loc[df['UID'] == 'Id_e45a3682']
#pat1.head(25)
patientTab = pd.crosstab(df['Age_bin'],df['Event_freq'])
stats.chi2_contingency(patientTab,correction=False)

(17715.63512077075,
 0.0,
 2097,
 array([[ 193.04351795,  206.5816348 ,  250.4551616 , ..., 2702.60925133,
         2969.61100019, 7454.73896923],
        [ 194.1159931 ,  207.72932248,  251.84659364, ..., 2717.62390338,
         2986.10901072, 7496.1546166 ],
        [ 193.23732666,  206.78903529,  250.70660953, ..., 2705.32257328,
         2972.59238224, 7462.22325757],
        [ 189.60316229,  202.90000743,  245.99163523, ..., 2654.44427201,
         2916.68760686, 7321.8831566 ]]))

In [11]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42, test_size=.33)
#regressor = DecisionTreeRegressor()
#lr = LinearRegression()
#model = clf.fit(X_train,y_train.values.ravel())
reg.fit(X_train, y_train)

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

...

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/usr/local/lib/python3.6/dist-packages/sklearn/m

GridSearchCV(cv=5, error_score='raise',
       estimator=DecisionTreeRegressor(criterion='mse', max_depth=None, max_features=None,
           max_leaf_nodes=None, min_impurity_decrease=0.0,
           min_impurity_split=None, min_samples_leaf=1,
           min_samples_split=2, min_weight_fraction_leaf=0.0,
           presort=False, random_state=None, splitter='best'),
       fit_params=None, iid=True, n_jobs=1,
       param_grid=[{'max_features': ['sqrt', 'log2', None], 'max_depth': range(2, 1000)}],
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='mean_squared_error', verbose=0)

In [12]:
print ("Grid scores on development set:")
for params, mean_score, scores in reg.grid_scores_:
    print ("%0.3f (+/-%0.03f) for %r" % (mean_score, scores.std() * 2, params))

Grid scores on development set:
-0.291 (+/-0.001) for {'max_depth': 2, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 2, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 2, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 3, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 3, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 3, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 4, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 4, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 4, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 5, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 5, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 5, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 6, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 6, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 6, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth

/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_search.py:761: DeprecationWarning: The grid_scores_ attribute was deprecated in version 0.18 in favor of the more elaborate cv_results_ attribute. The grid_scores_ attribute will not be available from 0.20
  DeprecationWarning)



-0.291 (+/-0.001) for {'max_depth': 249, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 250, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 250, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 250, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 251, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 251, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 251, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 252, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 252, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 252, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 253, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 253, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 253, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 254, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 254, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth'

-0.291 (+/-0.001) for {'max_depth': 987, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 987, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 987, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 988, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 988, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 988, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 989, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 989, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 989, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 990, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 990, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 990, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth': 991, 'max_features': 'sqrt'}
-0.291 (+/-0.001) for {'max_depth': 991, 'max_features': 'log2'}
-0.291 (+/-0.001) for {'max_depth': 991, 'max_features': None}
-0.291 (+/-0.001) for {'max_depth':

In [14]:
y_pred = reg.predict(X_test)

In [17]:
from sklearn.metrics import r2_score
r2_score(y_test,y_pred) 

0.2502066776355914

In [18]:
from sklearn.metrics import mean_squared_error
mean_squared_error(y_pred, y_test)

0.29151108805925113